In [1]:
import pandas as pd
import numpy as np 
import glob
import os 

In [2]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "EUDORA"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 3).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [3]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO   MARCA       Date  NUM_CICLO  \
2430  C202515   2025-10-08 2025-10-28       21  EUDORA 2025-10-08         15   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  match  
2430     C2025    C202518               50      1

In [4]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C15\SIMILARES\PRODUTOS SIMILARES - EUD.xlsx")

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO',
       'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [5]:
df_similares.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'CAMPANHA', 'MATCH'],
      dtype='object')

In [6]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C15\tabela de pedido\Pedidos Semanais Especiais - GKD - 202515.xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

#df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [7]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv = df_pdv[df_pdv['CANAL'].isin(['HIB','VD', 'CD'])]

df_pdv = df_pdv[df_pdv['STATUS'] == 'ATIVO']

df_pdv['PDV DESC'] = df_pdv['DESCRIÇÃO PDV']

df_pdv['MATCH'] = 1

In [8]:
df_pdv[df_pdv['PDV']==24255]

PDV CANAL DESCRIÇÃO PDV  PDV DESC   UF ANALISTA  \
77  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   

                    SUPERVISOR STATUS  MATCH  
77  Arianne Sodré [Provisório]  ATIVO      1

In [9]:
df_pdv.columns

Index(['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA',
       'SUPERVISOR', 'STATUS', 'MATCH'],
      dtype='object')

In [10]:
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [11]:
df_similares[df_similares['PDV'] == 24255]

PRODUTO LANÇAMENTO                   DESCRIÇÃO DO LANÇAMENTO  \
26                 86312                    DIVA CREM HID MAOS 50g   
57                 84959  EUD MAKE BAS LIQ CONTR SK/PERF 100F 30ml   
88                 84960  EUD MAKE BAS LIQ CONTR SK/PERF 120N 30ml   
119                84962  EUD MAKE BAS LIQ CONTR SK/PERF 140Q 30ml   
150                84963  EUD MAKE BAS LIQ CONTR SK/PERF 170Q 30ml   
...                  ...                                       ...   
2475               19047                19047 COMBO TRIO BÁSICO 30   
2506               52168       NEO DERMO GEL LIMP FAC PURIFIC 150g   
2537               52038     NEO DERMO CR ANTIS FAC 30 PRO AGE 50g   
2568               19048                      COMBO TRIO BASICO 45   
2599               52033     NEO DERMO CR ANTIS FAC 45 PRO AGE 50g   

      PRODUTO SIMILAR                      DESCRIÇÃO SIMILAR CICLO SIMILAR  \
26              93924     DIVA CREM HID MAOS ESPLENDIDA 50g]       C202202   
57              50634     GLAM BASE LIQ SK/CONTR COR 00 30ml       C202305   
88              50630     GLAM BASE LIQ SK/CONTR COR 05 30ml       C202305   
119             50629     GLAM BASE LIQ SK/CONTR COR 10 30ml       C202305   
150             50628     GLAM BASE LIQ SK/CONTR COR 15 30ml       C202305   
...               ...                                    ...           ...   
2475                0                                      0             0   
2506            52168    NEO DERMO GEL LIMP FAC PURIFIC 150g       C202311   
2537            52038  NEO DERMO CR ANTIS FAC 30 PRO AGE 50g       C202308   
2568                0                                      0             0   
2599            52038  NEO DERMO CR ANTIS FAC 30 PRO AGE 50g       C202308   

     FOCO  IAF            CATEGORIA        MARCA          % CONSUMIDOR  ...  \
26    Não  Não  CUIDADOS COM A PELE         DIVA                  0,00  ...   
57    Não  Não            MAQUIAGEM  EUDORA MAKE                  0,00  ...   
88    Não  Não            MAQUIAGEM  EUDORA MAKE                  0,00  ...   
119   Não  Não            MAQUIAGEM  EUDORA MAKE                  0,00  ...   
150   Não  Não            MAQUIAGEM  EUDORA MAKE                  0,00  ...   
...   ...  ...                  ...          ...                   ...  ...   
2475    0    0                    0            0                     0  ...   
2506  Não  Não     CUIDADOS FACIAIS    NEO DERMO  19,34 | 25,14 | 7,00  ...   
2537  Não  Não     CUIDADOS FACIAIS    NEO DERMO  20,09 | 25,14 | 7,00  ...   
2568    0    0                    0            0                     0  ...   
2599  Não  Não     CUIDADOS FACIAIS    NEO DERMO  20,09 | 25,14 | 7,00  ...   

         CAMPANHA MATCH    PDV CANAL DESCRIÇÃO PDV  PDV DESC   UF ANALISTA  \
26    Lançamentos     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
57    Lançamentos     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
88    Lançamentos     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
119   Lançamentos     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
150   Lançamentos     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
...           ...   ...    ...   ...           ...       ...  ...      ...   
2475            0     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
2506    Promoções     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
2537    Promoções     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
2568            0     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   
2599    Promoções     1  24255    VD      VD Irecê  VD Irecê  BA3     LAIS   

                      SUPERVISOR STATUS  
26    Arianne Sodré [Provisório]  ATIVO  
57    Arianne Sodré [Provisório]  ATIVO  
88    Arianne Sodré [Provisório]  ATIVO  
119   Arianne Sodré [Provisório]  ATIVO  
150   Arianne Sodré [Provisório]  ATIVO  
...                          ...    ...  
2475  Arianne Sodré [Provisório]  ATIVO  
2506  

In [12]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C15\arquivos para geração da sugestão\DRAFT"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft['match'] = 1 

df_draft.shape


(84064, 46)

In [13]:
df_draft = df_draft.drop(columns=['Categoria'])

In [14]:
df_draft.columns[7:25]

Index(['Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [15]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[7:25]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_33884\1463083786.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)


In [16]:
df_similares['PDV'] = df_similares['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [17]:
import pyodbc
import configparser


config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = '''
SELECT 
    b.[DATA] AS Dia,
    b.pdv AS PDV,
    b.sku as 'Código do Produto',
    b.VENDAS AS Quantidade
FROM base_vendas_bi b
LEFT JOIN (
    SELECT SKU, MAX(ORIGEM) AS ORIGEM
    FROM estoque_mar
    GROUP BY SKU
) e ON b.SKU = e.SKU
'''
dfi = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_33884\330515216.py:29: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql(query, conn)


In [18]:
dfi.head()

Dia    PDV  Código do Produto Quantidade
0  2025-06-02  20998              82113          0
1  2025-06-10  20998              82113          1
2  2025-06-05  20998              85299          2
3  2025-06-06  20998              85299          0
4  2025-06-04  20998              85299          2

In [19]:
df_venda_diaria = dfi 

In [20]:
df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], errors='coerce').dt.strftime('%d/%m/%Y')

In [21]:
#df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\EUDORA\C13\venda diaria\FormFiltroConsultaVendaSintetica_10_07_2025_15_27_42.xls")

df_venda_diaria.head()

Dia    PDV  Código do Produto Quantidade
0  02/06/2025  20998              82113          0
1  10/06/2025  20998              82113          1
2  05/06/2025  20998              85299          2
3  06/06/2025  20998              85299          0
4  04/06/2025  20998              85299          2

In [22]:
df_venda_diaria.head()

Dia    PDV  Código do Produto Quantidade
0  02/06/2025  20998              82113          0
1  10/06/2025  20998              82113          1
2  05/06/2025  20998              85299          2
3  06/06/2025  20998              85299          0
4  04/06/2025  20998              85299          2

In [23]:
df_venda_diaria.dtypes

Dia                  object
PDV                  object
Código do Produto     int64
Quantidade           object
dtype: object

In [24]:
df_venda_diaria['Quantidade'] = df_venda_diaria['Quantidade'].astype('float')

In [25]:
df_venda_diaria.columns

Index(['Dia', 'PDV', 'Código do Produto', 'Quantidade'], dtype='object')

In [26]:
#df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

df_venda_diaria = df_venda_diaria.drop(columns='Date')

df_venda_diaria.shape

(6931145, 5)

In [27]:
# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['PDV', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_venda_diaria['Quantidade Acumulada'] = (
    df_venda_diaria
    .groupby(['PDV', 'Código do Produto'])['Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_venda_diaria.shape

(6931145, 6)

In [28]:
df_venda_diaria = df_venda_diaria.drop_duplicates()

df_venda_agrupado = df_venda_diaria.groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade Acumulada'].max().reset_index()
df_venda_agrupado

PDV  Código do Produto    Ciclo  Quantidade Acumulada
0        11111              48130  C202309                   0.0
1        11201               1004  C202509                   0.0
2        11201               1005  C202509                   0.0
3        11201               1078  C202509                   0.0
4        11201               1296  C202509                   0.0
...        ...                ...      ...                   ...
2339197   5699              90772  C202511                   0.0
2339198   5699              90774  C202511                   0.0
2339199   5699              90774  C202512                   3.0
2339200   5699              90776  C202511                   0.0
2339201   8074              43151  C202505                   0.0

[2339202 rows x 4 columns]

In [29]:
df_venda_agrupado['Quantidade Acumulada'].sum()

np.float64(211020534.731)

In [30]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

(2604, 75)

In [31]:
#df_final = df_final.drop(columns=['PDV DESC','status','SKU','Descrição','Lançamento','Item analisado','Planograma','Quantidade por caixa'])

In [32]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [33]:

df_venda_agrupado = df_venda_agrupado.rename(columns={'Quantidade Acumulada':'Vendas Ciclo Lançamento'})

In [34]:
df_final['PRODUTO LANÇAMENTO'] = df_final['PRODUTO LANÇAMENTO'].astype('Int64')

df_venda_agrupado['PDV'] = df_venda_agrupado['PDV'].astype('Int64')

df_final = pd.merge(left=df_final, right = df_venda_agrupado, right_on=['Ciclo','Código do Produto','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [35]:
df_final['PDV'].value_counts().min()

np.int64(84)

In [36]:
df_final.columns[30:47]

Index(['Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511'],
      dtype='object')

In [37]:
colunas = df_final.columns[30:47]

df_final[colunas] = df_final[colunas].fillna(0)


In [38]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[30:47]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


np.float64(0.0812)

In [39]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [40]:
VENDA_SIMILAR_6_MESES= df_final.columns[40:47]

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)


df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].dropna().median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[colunas_mensais].dropna().mean(axis=1)

df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)

In [41]:
df_final['MEDIANA DO HISTÓRICO USADA'] = np.where(df_final['MEDIA DO HISTÓRICO']<df_final['MEDIANA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'],df_final['MEDIA DO HISTÓRICO'])



In [42]:
df_depara_vdc = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\Filiais - Vitoria da Conquista 4.xlsx")


df_vdc = pd.read_parquet(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\Vitoria da Conquista\HISTORICO VENDAS VITORIA DA CONQUISTA\VENDAS VITORIA DA CONQUISTA\concatenado.parquet")

df_vdc['PDV'] = df_vdc['Quebra'].str.split(" -").str[0]

df_vdc['PDV'] = df_vdc['PDV'].astype('int64')

df_vdc = df_vdc.rename(columns={'Quebra2':'DATA VENDA'})

df_vdc['DATA VENDA'] = pd.to_datetime(df_vdc['DATA VENDA'], format='%d/%m/%Y')

df_vdc = pd.merge(df_vdc,df_depara_vdc[['CP VIVA BEM','PDVDEPARA.Practico']],left_on='PDV',right_on='CP VIVA BEM',how='inner')

df_vdc['Quantidade'] = df_vdc['Quantidade'].str.replace(r',000$','',regex=True)

df_vdc['Quantidade'] = df_vdc['Quantidade'].astype('Int64') 

########################################
df_vdc['Quantidade Acumulada vdc'] = (
        df_vdc
        .groupby(['PDVDEPARA.Practico', 'Código'])['Quantidade']
        .cumsum())


In [43]:
df_vdc['PDVDEPARA.Practico'] = df_vdc['PDVDEPARA.Practico'].astype(str).str.replace(r'\.0$', '', regex=True)

df_vdc['PDVDEPARA.Practico'].head()

0    23713
1    23713
2    23713
3    23713
4    23713
Name: PDVDEPARA.Practico, dtype: object

In [44]:
df_vdc = pd.merge(left=df_vdc,right=calendario[['Date','Ciclo']],left_on='DATA VENDA',right_on='Date',how='inner')

df_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',	'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()

df_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})

df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].fillna(0)

df_vdc_agrupado.head()

PDVDEPARA.Practico  Código Ciclo vdc  Quantidade Acumulada vdc
0              23701    1004   C202301                     164.0
1              23701    1004   C202302                     167.0
2              23701    1004   C202303                     170.0
3              23701    1004   C202304                     173.0
4              23701    1004   C202305                     180.0

In [45]:
df_vdc_agrupado = df_vdc_agrupado[df_vdc_agrupado['PDVDEPARA.Practico'] != 'nan']

In [46]:
df_vdc_agrupado['PDVDEPARA.Practico'] = df_vdc_agrupado['PDVDEPARA.Practico'].astype('Int64')

In [47]:
df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada vdc'] = df_final['Quantidade Acumulada vdc'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc']>0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada vdc')


df_final = df_final.drop(columns='Ciclo vdc')



In [48]:
df_final.columns[40:47]

Index(['Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511'],
      dtype='object')

In [49]:
medi = df_final.groupby(['CANAL','UF'])['MEDIANA DO HISTÓRICO USADA'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO USADA':'med_por_canal'})
medi

CANAL   UF  med_por_canal
0     CD   AL      60.176471
1    HIB   AL      15.117647
2    HIB   BA       0.941176
3    HIB  BA3       0.470588
4    HIB   SE       6.941176
5    HIB  VDC       0.411765
6     VD   AL      42.705882
7     VD   BA       1.588235
8     VD  BA3       0.823529
9     VD   SE      26.352941
10    VD  VDC       2.647059

In [50]:
df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF'],how='inner')




In [51]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + CRESCIMENTO #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + CRESCIMENTO>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + CRESCIMENTO)

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

#df_final['MEDIANA DO HISTÓRICO USADA'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0, df_final['med_por_canal'],df_final['MEDIANA DO HISTÓRICO'])


In [52]:
df_final['med_por_canal'].isna().sum()

np.int64(0)

In [53]:

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final['Vendas Ciclo Lançamento'] + df_final['Vendas Ciclo Lançamento'] < df_final['MEDIANA DO HISTÓRICO USADA'],
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO USADA']+ df_final['MEDIANA DO HISTÓRICO USADA'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final['Vendas Ciclo Lançamento']+df_final['Vendas Ciclo Lançamento'],0))

df_final['PV GINSENG'] = np.where(df_final['PV GINSENG'].isna(),df_final['med_por_canal'] ,df_final['PV GINSENG'])

df_final.shape

(2604, 91)

In [54]:
df_final.drop(columns=df_final.columns[29:42],inplace=True)

In [55]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'CAMPANHA', 'MATCH', 'PDV',
       'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'STATUS', 'Classe', 'SKU', 'Descrição', 'Subcategoria', 'Lançamento',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo Atual', 'Dias sem venda',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1',
       'Promoção Próximo Ciclo', 'Promoção Próximo Ciclo + 1', 'Estoque Atual',
       'Estoque em Transito', 'Pedido Pendente',
       'Compra inteligente semanal/Sugestão de compra',
       'C

In [56]:

df_final.drop(columns=['STATUS', 'Classe', 'SKU', 'Subcategoria', 'Lançamento',
       'Dias sem venda',
       #'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1',
       'Promoção Próximo Ciclo', 'Promoção Próximo Ciclo + 1', 'Estoque Atual',
       'Estoque em Transito', 'Pedido Pendente',
       'Compra inteligente semanal/Sugestão de compra',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Item Desativado',
       'Data Prevista Regularização', 'Carteira Bloqueada Para Novos Pedidos',
       'Planograma', 'Quantidade por caixa', 'Preço Sell In', 'Quantidade',
       'Item analisado', 'match_x',
        'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'match_y', 'dias_ate_inicio', 'INICIO CICLO SIMILAR','med_por_canal', 'CRESCIMENTO_FINAL',
       'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR', 'Código do Produto','CRESCIMENTO_GERAL'],inplace=True)
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'CAMPANHA', 'MATCH', 'PDV',
       'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'Descrição', 'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo Atual', 'Projeção Próximo Ciclo',
       'Projeção Próximo Ciclo + 1', 'CRESCIMENTO', 'Vendas Ciclo Lançamento',
       'Pico Vendas Similar Ultimos 6 ciclos', 'MEDIANA DO HISTÓRICO',
       'MEDIA DO HISTÓRICO', 'MEDIANA DO HISTÓRICO USADA',
       'PDVDEPARA.Practico', 'Código', 'PV GINSENG'],
      dtype='object')

In [57]:
df_final.columns[25:30]

Index(['Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo 202509',
       'Histórico de Vendas do Ciclo 202510',
       'Histórico de Vendas do Ciclo 202511',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [58]:
df_final = df_final.rename(columns={df_final.columns[25]: "C-4", df_final.columns[26]: "C-3",df_final.columns[27]: "C-2",df_final.columns[28]: "C-1",df_final.columns[29]:'VENDAS CICLO ATUAL'})


In [59]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='HISTÓRICO DE VENDAS DO CICLO').columns, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'CAMPANHA', 'MATCH', 'PDV',
       'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'DESCRIÇÃO', 'C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL',
       'PROJEÇÃO PRÓXIMO CICLO', 'PROJEÇÃO PRÓXIMO CICLO + 1', 'CRESCIMENTO',
       'VENDAS CICLO LANÇAMENTO', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
       'MEDIANA DO HISTÓRICO', 'MEDIA DO HISTÓRICO',
       'MEDIANA DO HISTÓRICO USADA', 'PDVDEPARA.PRACTICO', 'CÓDIGO',
       'PV GINSENG'],
      dtype='object')

In [60]:
df_final = df_final.drop(columns=['DESCRIÇÃO','MEDIANA DO HISTÓRICO'])

In [61]:
df_final.shape

(2604, 38)

In [62]:
df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'CAMPANHA', 'MATCH', 'PDV',
       'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF', 'ANALISTA', 'SUPERVISOR',
       'C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL',
       'PROJEÇÃO PRÓXIMO CICLO', 'PROJEÇÃO PRÓXIMO CICLO + 1', 'CRESCIMENTO',
       'VENDAS CICLO LANÇAMENTO', 'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
       'MEDIA DO HISTÓRICO', 'MEDIANA DO HISTÓRICO USADA',
       'PDVDEPARA.PRACTICO', 'CÓDIGO', 'PV GINSENG'],
      dtype='object')

In [63]:
CRESCIMENTO

np.float64(0.0812)

In [64]:
df_final = df_final.reindex(columns=[
    'SUPERVISOR',
    'CANAL',
    'UF',
    'PDV',
    'PDV DESC',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG',
    'PROJEÇÃO PRÓXIMO CICLO',
    'PROJEÇÃO PRÓXIMO CICLO + 1',
    ])


In [65]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [66]:
df_final['PV GINSENG'] = np.ceil(df_final['PV GINSENG'])

In [67]:
df_final.to_excel(r'C:\Users\joao.herculano\Documents\lançamentosugestEUD2.xlsx',index=False)